In [1]:
import json
import os
import numpy as np
from sklearn.model_selection import StratifiedGroupKFold
from pycocotools.coco import COCO

# load json 
annotation = './dataset/train_ann_len_under_40.json'
coco = COCO(annotation)

with open(annotation) as f: data = json.load(f)

var = [(ann['image_id'], ann['category_id']) for ann in data['annotations']]
X = np.ones((len(data['annotations']),1))
y = np.array([v[1] for v in var])
groups = np.array([v[0] for v in var])

cv = StratifiedGroupKFold(n_splits=5, shuffle=True, random_state=7)

# fold별 train, val set을 coco에서 file_name을 가져와 txt파일로 저장
for idx, (train_idx, val_idx) in enumerate(cv.split(X, y, groups)):
    train_img_ids = groups[train_idx]
    val_img_ids = groups[val_idx]
    train_img_ids = list(set(train_img_ids))
    val_img_ids = list(set(val_img_ids))
    train_img_names = [coco.imgs[img_id]['file_name'] for img_id in train_img_ids]
    val_img_names = [coco.imgs[img_id]['file_name'] for img_id in val_img_ids]

    os.makedirs(f'./ultralytics_dataset/fold_{idx}', exist_ok=True)

    with open(f'./ultralytics_dataset/fold_{idx}/train_fold_{idx}.txt', 'w') as f:
        for img_name in train_img_names:
            f.write(f"/home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/fold_{idx}/train/images/"+img_name.replace('train/', '')+'\n')

    with open(f'./ultralytics_dataset/fold_{idx}/val_fold_{idx}.txt', 'w') as f:
        for img_name in val_img_names:
            f.write(f"/home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/fold_{idx}/val/images/"+img_name.replace('train/', '')+'\n')

    for i in ['train', 'val']:
        os.makedirs(f'./ultralytics_dataset/fold_{idx}/{i}/images', exist_ok=True)
        os.makedirs(f'./ultralytics_dataset/fold_{idx}/{i}/labels', exist_ok=True)

    for img_name in train_img_names:
        os.system(f'cp ./dataset/{img_name} ./ultralytics_dataset/fold_{idx}/train/images/')
        os.system(f'cp ./dataset/labels/{img_name.removeprefix('train/').replace("jpg", "txt").replace('/train', '')} ./ultralytics_dataset/fold_{idx}/train/labels/')

    for img_name in val_img_names:
        os.system(f'cp ./dataset/{img_name} ./ultralytics_dataset/fold_{idx}/val/images/')
        os.system(f'cp ./dataset/labels/{img_name.removeprefix('train/').replace("jpg", "txt")} ./ultralytics_dataset/fold_{idx}/val/labels/')

    import shutil
    shutil.copyfile('./ultralytics_dataset/test.txt', f'./ultralytics_dataset/fold_{idx}/test.txt')


    import yaml

    # 데이터셋 루트 경로 설정
    dataset_path = f"/home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/fold_{idx}/"

    # YAML 파일에 들어갈 정보 설정
    data = {
        'path': dataset_path,  # 데이터셋 루트 경로
        'train': f'train_fold_{idx}.txt',  # 학습 데이터 경로
        'val': f'val_fold_{idx}.txt',      # 검증 데이터 경로
        'test': 'test.txt',    # 테스트 데이터 경로
        'names': {
            0: 'General trash',
            1: 'Paper',
            2: 'Paper pack',
            3: 'Metal',
            4: 'Glass',
            5: 'Plastic',
            6: 'Styrofoam',
            7: 'Plastic bag',
            8: 'Battery',
            9: 'Clothing'
        }
    }

    # YAML 파일 생성
    yaml_path = f'dataset_yaml/rtdetr_fold_{idx}.yaml'
    with open(yaml_path, 'w') as yaml_file:
        yaml.dump(data, yaml_file, default_flow_style=False, allow_unicode=True)
    
    break

loading annotations into memory...
Done (t=0.05s)
creating index...
index created!


In [8]:
# check distribution
import pandas as pd
from collections import Counter

def get_distribution(y):
    y_distr = Counter(y)
    y_vals_sum = sum(y_distr.values())

    return [f'{y_distr[i]/y_vals_sum:.2%}' for i in range(np.max(y) +1)]

distrs = [get_distribution(y)]
index = ['training set']

for fold_ind, (train_idx, val_idx) in enumerate(cv.split(X,y, groups)):
    train_y, val_y = y[train_idx], y[val_idx]
    train_gr, val_gr = groups[train_idx], groups[val_idx]

    assert len(set(train_gr) & set(val_gr)) == 0 
    
    distrs.append(get_distribution(train_y))
    distrs.append(get_distribution(val_y))
    index.append(f'train - fold{fold_ind}')
    index.append(f'val - fold{fold_ind}')

categories = [d['name'] for d in data['categories']]
pd.DataFrame(distrs, index=index, columns = [categories[i] for i in range(np.max(y) + 1)])

General trash   Paper Paper pack  Metal  Glass Plastic  \
training set         17.70%  26.60%      3.75%  3.91%  4.21%  12.69%   
train - fold0        17.54%  27.15%      3.84%  3.86%  4.33%  12.33%   
val - fold0          18.40%  24.27%      3.39%  4.16%  3.68%  14.19%   
train - fold1        17.71%  27.09%      3.71%  3.83%  3.93%  12.50%   
val - fold1          17.65%  24.64%      3.92%  4.25%  5.32%  13.44%   
train - fold2        17.73%  26.22%      3.69%  3.92%  3.94%  12.69%   
val - fold2          17.59%  28.07%      4.00%  3.89%  5.23%  12.68%   
train - fold3        17.84%  25.65%      3.81%  3.98%  4.53%  13.04%   
val - fold3          17.17%  30.37%      3.52%  3.64%  2.96%  11.29%   
train - fold4        17.69%  26.90%      3.71%  3.98%  4.31%  12.88%   
val - fold4          17.75%  25.44%      3.90%  3.65%  3.81%  11.92%   

              Styrofoam Plastic bag Battery Clothing  
training set      5.31%      22.93%   0.75%    2.15%  
train - fold0     5.32%      22.85%   0.66%    2.13%  
val - fold0       5.28%      23.25%   1.15%    2.24%  
train - fold1     5.20%      23.02%   0.75%    2.25%  
val - fold1       5.74%      22.56%   0.73%    1.75%  
train - fold2     5.40%      23.44%   0.71%    2.26%  
val - fold2       4.96%      20.96%   0.89%    1.73%  
train - fold3     5.46%      22.74%   0.77%    2.18%  
val - fold3       4.69%      23.68%   0.65%    2.03%  
train - fold4     5.16%      22.59%   0.85%    1.93%  
val - fold4       5.89%      24.27%   0.35%    3.02%

In [ ]:
import json
import os
from datetime import datetime

import numpy as np
from sklearn.model_selection import StratifiedGroupKFold
from pycocotools.coco import COCO
from tqdm import tqdm
from ultralytics import RTDETR
import pandas as pd
import wandb

wandb.login(key="20ced4618a33e8061ca7264d38e0409df13c8daa")

from ultralytics.data.augment import Albumentations
from ultralytics.utils import LOGGER, colorstr

# load json 
annotation = './dataset/train_ann_len_under_40.json'
coco = COCO(annotation)

with open(annotation) as f: data = json.load(f)

var = [(ann['image_id'], ann['category_id']) for ann in data['annotations']]
X = np.ones((len(data['annotations']),1))
y = np.array([v[1] for v in var])
groups = np.array([v[0] for v in var])

cv = StratifiedGroupKFold(n_splits=5, shuffle=True, random_state=7)

# fold별 train, val set을 coco에서 file_name을 가져와 txt파일로 저장
for idx, (train_idx, val_idx) in enumerate(cv.split(X, y, groups)):
    train_img_ids = groups[train_idx]
    val_img_ids = groups[val_idx]
    train_img_ids = list(set(train_img_ids))
    val_img_ids = list(set(val_img_ids))
    train_img_names = [coco.imgs[img_id]['file_name'] for img_id in train_img_ids]
    val_img_names = [coco.imgs[img_id]['file_name'] for img_id in val_img_ids]

    os.makedirs(f'./ultralytics_dataset/fold_{idx}', exist_ok=True)

    with open(f'./ultralytics_dataset/fold_{idx}/train_fold_{idx}.txt', 'w') as f:
        for img_name in train_img_names:
            f.write(f"/home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/fold_{idx}/train/images/"+img_name.replace('train/', '')+'\n')

    with open(f'./ultralytics_dataset/fold_{idx}/val_fold_{idx}.txt', 'w') as f:
        for img_name in val_img_names:
            f.write(f"/home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/fold_{idx}/val/images/"+img_name.replace('train/', '')+'\n')

    for i in ['train', 'val']:
        os.makedirs(f'./ultralytics_dataset/fold_{idx}/{i}/images', exist_ok=True)
        os.makedirs(f'./ultralytics_dataset/fold_{idx}/{i}/labels', exist_ok=True)

    for img_name in train_img_names:
        os.system(f'cp ./dataset/{img_name} ./ultralytics_dataset/fold_{idx}/train/images/')
        os.system(f'cp ./dataset/labels/{img_name.removeprefix('train/').replace("jpg", "txt").replace('/train', '')} ./ultralytics_dataset/fold_{idx}/train/labels/')

    for img_name in val_img_names:
        os.system(f'cp ./dataset/{img_name} ./ultralytics_dataset/fold_{idx}/val/images/')
        os.system(f'cp ./dataset/labels/{img_name.removeprefix('train/').replace("jpg", "txt")} ./ultralytics_dataset/fold_{idx}/val/labels/')

    import shutil
    shutil.copyfile('./ultralytics_dataset/test.txt', f'./ultralytics_dataset/fold_{idx}/test.txt')


    import yaml

    # 데이터셋 루트 경로 설정
    dataset_path = f"/home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/fold_{idx}/"

    # YAML 파일에 들어갈 정보 설정
    data = {
        'path': dataset_path,  # 데이터셋 루트 경로
        'train': f'train_fold_{idx}.txt',  # 학습 데이터 경로
        'val': f'val_fold_{idx}.txt',      # 검증 데이터 경로
        'test': 'test.txt',    # 테스트 데이터 경로
        'names': {
            0: 'General trash',
            1: 'Paper',
            2: 'Paper pack',
            3: 'Metal',
            4: 'Glass',
            5: 'Plastic',
            6: 'Styrofoam',
            7: 'Plastic bag',
            8: 'Battery',
            9: 'Clothing'
        }
    }

    # YAML 파일 생성
    yaml_path = f'dataset_yaml/rtdetr_fold_{idx}.yaml'
    with open(yaml_path, 'w') as yaml_file:
        yaml.dump(data, yaml_file, default_flow_style=False, allow_unicode=True)
    
    from ultralytics.data.augment import Albumentations
    from ultralytics.utils import LOGGER, colorstr


    def __init__(self, p=1.0):
        self.p = p
        self.transform = None
        prefix = colorstr("albumentations: ")

        try:
            import albumentations as A

            # List of possible spatial transforms
            spatial_transforms = {
                "Affine",
                "BBoxSafeRandomCrop",
                "CenterCrop",
                "CoarseDropout",
                "Crop",
                "CropAndPad",
                "CropNonEmptyMaskIfExists",
                "D4",
                "ElasticTransform",
                "Flip",
                "GridDistortion",
                "GridDropout",
                "HorizontalFlip",
                "Lambda",
                "LongestMaxSize",
                "MaskDropout",
                "MixUp",
                "Morphological",
                "NoOp",
                "OpticalDistortion",
                "PadIfNeeded",
                "Perspective",
                "PiecewiseAffine",
                "PixelDropout",
                "RandomCrop",
                "RandomCropFromBorders",
                "RandomGridShuffle",
                "RandomResizedCrop",
                "RandomRotate90",
                "RandomScale",
                "RandomSizedBBoxSafeCrop",
                "RandomSizedCrop",
                "Resize",
                "Rotate",
                "SafeRotate",
                "ShiftScaleRotate",
                "SmallestMaxSize",
                "Transpose",
                "VerticalFlip",
                "XYMasking",
            }  # from https://albumentations.ai/docs/getting_started/transforms_and_targets/#spatial-level-transforms

            # Transforms
            T = [
                A.Blur(p=0.3),
                A.ToGray(p=0.3),
                A.CLAHE(p=0.3),
                A.RandomBrightnessContrast(p=0.3),
                A.HueSaturationValue(p=0.3),
                A.RandomSnow(p=0.3),
                A.HorizontalFlip(p=0.5),
            ]

            # Compose transforms
            self.contains_spatial = any(
                transform.__class__.__name__ in spatial_transforms for transform in T
            )
            self.transform = (
                A.Compose(
                    T,
                    bbox_params=A.BboxParams(format="yolo", label_fields=["class_labels"]),
                )
                if self.contains_spatial
                else A.Compose(T)
            )
            LOGGER.info(
                prefix
                + ", ".join(f"{x}".replace("always_apply=False, ", "") for x in T if x.p)
            )
        except ImportError:  # package not installed, skip
            pass
        except Exception as e:
            LOGGER.info(f"{prefix}{e}")


    Albumentations.__init__ = __init__

    # COCO 사전 훈련된 RT-DETR-l 모델 로드
    model = RTDETR("rtdetr-l.pt")
    model.train(
        data=yaml_path,
        epochs=40,
        imgsz=1024,
        batch=8,
        device=[1],
        cache="disk",
        project="Ultralytics",
        name="RT-DETR-l",
    )
    validations = model.val(data_yaml=yaml_path, batch_size=8, img_size=1024, iou_thres=0.7, save_json=True, save_txt=True)

#### fold별 추론

#### 결과 앙상블

In [5]:
!pip install ensemble_boxes

{'metrics/precision(B)': 0.8510079093550562,
 'metrics/recall(B)': 0.6553374095716663,
 'metrics/mAP50(B)': 0.7301296009268983,
 'metrics/mAP50-95(B)': 0.6371883944488608,
 'fitness': 0.6464825150966645}

In [7]:
import pandas as pd
import numpy as np
from ensemble_boxes import nms
from pycocotools.coco import COCO
from ultralytics import RTDETR
from tqdm import tqdm

In [8]:
submission_df = []
for model in ['./Ultralytics/RT-DETR-l49/weights/best.pt', './Ultralytics/RT-DETR-l50/weights/best.pt', './Ultralytics/RT-DETR-l51/weights/best.pt', './Ultralytics/RT-DETR-l52/weights/best.pt', './Ultralytics/RT-DETR-l53/weights/best.pt']:
    model = RTDETR(model)
    results = model.predict(source="ultralytics_dataset/test/images", augment=True)
    # COCO 형식으로 저장할 데이터를 담을 딕셔너리
    csv_data = {}
    for result in tqdm(results):
        image_id = (
            result.path.split("/")[-3] + "/" + result.path.split("/")[-1]
        )  # 파일 이름에서 image_id 추출
        width, height = (
            result.orig_shape[1],
            result.orig_shape[0],
        )  # 이미지의 원본 크기 (width, height)
        prediction_string = ""
        for box in result.boxes:
            # YOLO 형식에서 COCO 형식으로 변환 (상대 좌표를 절대 좌표로 변환)
            bbox = box.xywh.tolist()[
                0
            ]  # YOLO 형식에서 [x_center, y_center, width, height] 가져옴 (상대 좌표)
            # 상대 좌표 (비율)를 절대 좌표 (픽셀 단위)로 변환
            x_center, y_center, w, h = bbox
            x_min = max(0, x_center - w / 2)
            y_min = max(0, y_center - h / 2)
            x_max = min(width, x_center + w / 2)
            y_max = min(height, y_center + h / 2)

            category_id = int(box.cls.item())
            score = box.conf.item()

            # COCO 형식으로 bbox 저장
            bbox_str = f"{x_min} {y_min} {x_max} {y_max}"

            # 같은 image_id의 예측 결과를 한 줄로 합침
            prediction_string += f"{category_id} {score} {bbox_str} "

        # image_id에 대해 기존 예측이 있으면 이어 붙임
        if image_id in csv_data:
            csv_data[image_id] += prediction_string
        else:
            csv_data[image_id] = prediction_string

    # 최종적으로 image_id와 PredictionString을 CSV로 저장
    df = pd.DataFrame(
        [
            {"PredictionString": pred_str, "image_id": image_id}
            for image_id, pred_str in csv_data.items()
        ]
    )

    submission_df.append(df)




WARNING ⚠️ inference results will accumulate in RAM unless `stream=True` is passed, causing potential out-of-memory
errors for large sources or long-running streams and videos. See https://docs.ultralytics.com/modes/predict/ for help.

Example:
    results = model(source=..., stream=True)  # generator of Results objects
    for r in results:
        boxes = r.boxes  # Boxes object for bbox outputs
        masks = r.masks  # Masks object for segment masks outputs
        probs = r.probs  # Class probabilities for classification outputs

image 1/4871 /home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/test/images/0000.jpg: 1024x1024 6 Papers, 1 Paper pack, 20 Plastics, 2 Styrofoams, 10 Plastic bags, 33.5ms
image 2/4871 /home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/test/images/0001.jpg: 1024x1024 2 Plastics, 2 Styrofoams, 33.4ms
image 3/4871 /home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultral

100%|██████████| 4871/4871 [00:04<00:00, 1128.67it/s]




WARNING ⚠️ inference results will accumulate in RAM unless `stream=True` is passed, causing potential out-of-memory
errors for large sources or long-running streams and videos. See https://docs.ultralytics.com/modes/predict/ for help.

Example:
    results = model(source=..., stream=True)  # generator of Results objects
    for r in results:
        boxes = r.boxes  # Boxes object for bbox outputs
        masks = r.masks  # Masks object for segment masks outputs
        probs = r.probs  # Class probabilities for classification outputs

image 1/4871 /home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/test/images/0000.jpg: 1024x1024 3 General trashs, 11 Papers, 1 Paper pack, 1 Metal, 16 Plastics, 11 Plastic bags, 38.7ms
image 2/4871 /home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/test/images/0001.jpg: 1024x1024 2 Plastics, 1 Styrofoam, 33.5ms
image 3/4871 /home/taeyoung4060ti/바탕화면/level2-objectdetection

100%|██████████| 4871/4871 [00:04<00:00, 1160.53it/s]




WARNING ⚠️ inference results will accumulate in RAM unless `stream=True` is passed, causing potential out-of-memory
errors for large sources or long-running streams and videos. See https://docs.ultralytics.com/modes/predict/ for help.

Example:
    results = model(source=..., stream=True)  # generator of Results objects
    for r in results:
        boxes = r.boxes  # Boxes object for bbox outputs
        masks = r.masks  # Masks object for segment masks outputs
        probs = r.probs  # Class probabilities for classification outputs

image 1/4871 /home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/test/images/0000.jpg: 1024x1024 2 General trashs, 4 Papers, 1 Paper pack, 14 Plastics, 9 Plastic bags, 33.7ms
image 2/4871 /home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/test/images/0001.jpg: 1024x1024 1 General trash, 1 Metal, 1 Glass, 1 Styrofoam, 33.8ms
image 3/4871 /home/taeyoung4060ti/바탕화면/level2-obj

100%|██████████| 4871/4871 [00:04<00:00, 1183.75it/s]




WARNING ⚠️ inference results will accumulate in RAM unless `stream=True` is passed, causing potential out-of-memory
errors for large sources or long-running streams and videos. See https://docs.ultralytics.com/modes/predict/ for help.

Example:
    results = model(source=..., stream=True)  # generator of Results objects
    for r in results:
        boxes = r.boxes  # Boxes object for bbox outputs
        masks = r.masks  # Masks object for segment masks outputs
        probs = r.probs  # Class probabilities for classification outputs

image 1/4871 /home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/test/images/0000.jpg: 1024x1024 1 General trash, 8 Papers, 2 Paper packs, 3 Plastics, 2 Styrofoams, 20 Plastic bags, 33.7ms
image 2/4871 /home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/test/images/0001.jpg: 1024x1024 1 General trash, 2 Plastics, 33.6ms
image 3/4871 /home/taeyoung4060ti/바탕화면/level2-objectde

100%|██████████| 4871/4871 [00:04<00:00, 1058.19it/s]




WARNING ⚠️ inference results will accumulate in RAM unless `stream=True` is passed, causing potential out-of-memory
errors for large sources or long-running streams and videos. See https://docs.ultralytics.com/modes/predict/ for help.

Example:
    results = model(source=..., stream=True)  # generator of Results objects
    for r in results:
        boxes = r.boxes  # Boxes object for bbox outputs
        masks = r.masks  # Masks object for segment masks outputs
        probs = r.probs  # Class probabilities for classification outputs

image 1/4871 /home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/test/images/0000.jpg: 1024x1024 3 Papers, 15 Plastics, 9 Plastic bags, 34.0ms
image 2/4871 /home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset/test/images/0001.jpg: 1024x1024 2 Plastics, 1 Styrofoam, 41.2ms
image 3/4871 /home/taeyoung4060ti/바탕화면/level2-objectdetection-cv-01/ultralytics-main/ultralytics_dataset

100%|██████████| 4871/4871 [00:04<00:00, 1174.16it/s]


In [9]:
image_ids = submission_df[0]['image_id'].tolist()

In [17]:
submission_df = [submission_df[0], submission_df[1], submission_df[2]]

In [18]:
# ensemble 할 file의 image 정보를 불러오기 위한 json
annotation = './dataset/test.json'
coco = COCO(annotation)

loading annotations into memory...
Done (t=0.01s)
creating index...
index created!


In [19]:
prediction_strings = []
file_names = []
# ensemble 시 설정할 iou threshold 이 부분을 바꿔가며 대회 metric에 알맞게 적용해봐요!
iou_thr = 0.4

# 각 image id 별로 submission file에서 box좌표 추출
for i, image_id in enumerate(image_ids):
    prediction_string = ''
    boxes_list = []
    scores_list = []
    labels_list = []
    image_info = coco.loadImgs(i)[0]
    # 각 submission file 별로 prediction box좌표 불러오기
    for df in submission_df:
        predict_string = df[df['image_id'] == image_id]['PredictionString'].tolist()[0]
        predict_list = str(predict_string).split()

        if len(predict_list)==0 or len(predict_list)==1:
            continue

        predict_list = np.reshape(predict_list, (-1, 6))
        box_list = []

        for box in predict_list[:, 2:6].tolist():
            # box의 각 좌표를 float형으로 변환한 후 image의 넓이와 높이로 각각 정규화
            image_width = image_info['width']
            image_height = image_info['height']
            box[0] = float(box[0]) / image_width
            box[1] = float(box[1]) / image_height
            box[2] = float(box[2]) / image_width
            box[3] = float(box[3]) / image_height
            box_list.append(box)

        boxes_list.append(box_list)
        scores_list.append(list(map(float, predict_list[:, 1].tolist())))
        labels_list.append(list(map(int, predict_list[:, 0].tolist())))

    # 예측 box가 있다면 이를 ensemble 수행
    if len(boxes_list):
        # ensemble_boxes에서 import한 nms()를 사용하여 NMS 계산 수행
        # 👉 위의 코드에서 만든 정보들을 함수에 간단하게 적용해보세요!
        # nms에 필요한 인자: [NMS할 box의 lists, confidence score의 lists, label의 list, iou에 사용할 threshold]
        boxes, scores, labels = nms(boxes_list, scores_list, labels_list, iou_thr=iou_thr)
        for box, score, label in zip(boxes, scores, labels):
            prediction_string += str(label) + ' ' + str(score) + ' ' + str(box[0] * image_info['width']) + ' ' + str(box[1] * image_info['height']) + ' ' + str(box[2] * image_info['width']) + ' ' + str(box[3] * image_info['height']) + ' '

    prediction_strings.append(prediction_string)
    file_names.append(image_id)

In [20]:
submission = pd.DataFrame()
submission['PredictionString'] = prediction_strings
submission['image_id'] = file_names
import os
os.makedirs('./sample_submission', exist_ok=True)
submission.to_csv('./sample_submission/submission_ensemble.csv', index=None)
submission.head()

PredictionString       image_id
0  0 0.568617582321167 216.34576416015625 689.748...  test/0000.jpg
1  0 0.4156109690666199 639.71484375 650.29229736...  test/0001.jpg
2  0 0.8390372395515442 165.6407012939453 296.207...  test/0002.jpg
3  0 0.3335207402706146 0.2119140625 0.0 1023.607...  test/0003.jpg
4  0 0.7956175804138184 191.822265625 254.0947265...  test/0004.jpg